## Imports

In [1]:
# Imports

import pandas as pd
import numpy as np
from uszipcode import SearchEngine
from sklearn import preprocessing
import folium
from folium import plugins

from state_heatmapwithtime import *

In [2]:
# Reading in the provided CSV file

df = pd.read_csv("zillow_data.csv")
df.head()

RegionID  RegionName      City State              Metro CountyName  \
0     84654       60657   Chicago    IL            Chicago       Cook   
1     90668       75070  McKinney    TX  Dallas-Fort Worth     Collin   
2     91982       77494      Katy    TX            Houston     Harris   
3     84616       60614   Chicago    IL            Chicago       Cook   
4     93144       79936   El Paso    TX            El Paso    El Paso   

   SizeRank   1996-04   1996-05   1996-06  ...  2017-07  2017-08  2017-09  \
0         1  334200.0  335400.0  336500.0  ...  1005500  1007500  1007800   
1         2  235700.0  236900.0  236700.0  ...   308000   310000   312500   
2         3  210400.0  212200.0  212200.0  ...   321000   320600   320200   
3         4  498100.0  500900.0  503100.0  ...  1289800  1287700  1287400   
4         5   77300.0   77300.0   77300.0  ...   119100   119400   120000   

   2017-10  2017-11  2017-12  2018-01  2018-02  2018-03  2018-04  
0  1009600  1013300  1018700  1024400  1030700  1033800  1030600  
1   314100   315000   316600   318100   319600   321100   321800  
2   320400   320800   321200   321200   323000   326900   329900  
3  1291500  1296600  1299000  1302700  1306400  1308500  1307000  
4   120300   120300   120300   120300   120500   121000   121500  

[5 rows x 272 columns]

## Pre-Processing

In [3]:
# Setting index to zipcode
df = df.set_index(df["RegionName"])

# Reserving the state information, for later mapping
state_list = df["State"]

In [4]:
# Dropping metadata columns
df = df.drop(columns=["RegionID", "RegionName", "City", "State",
                      "Metro", "CountyName", "SizeRank"])

In [5]:
# Grabbing only data from 2004 onwards
df = df.loc[:,"2004-01":]

In [6]:
# Dropping any rows with null values
df.dropna(axis=0, inplace=True)

# Sanity Check
df.isnull().sum().sum()

0

In [7]:
# Creating an array of the normalized data
df_norm = preprocessing.normalize(df)

# Setting that array as a dataframe, with the same row/column labels as before
df_scaled = pd.DataFrame(df_norm, index=df.index, columns=df.columns)

In [8]:
# Exploring the data, post-processing
print(df_scaled.shape)
df_scaled.head()

(13836, 172)


2004-01   2004-02   2004-03   2004-04   2004-05   2004-06  \
RegionName                                                               
60657       0.066883  0.067228  0.067653  0.068149  0.068681  0.069238   
75070       0.062166  0.062530  0.063027  0.063524  0.063921  0.064219   
77494       0.065783  0.066152  0.066265  0.066123  0.065868  0.065641   
60614       0.069419  0.069590  0.069829  0.070130  0.070466  0.070828   
79936       0.056091  0.056559  0.057093  0.057694  0.058228  0.058762   

             2004-07   2004-08   2004-09   2004-10  ...   2017-07   2017-08  \
RegionName                                          ...                       
60657       0.069770  0.070239  0.070682  0.071116  ...  0.089039  0.089216   
75070       0.064418  0.064617  0.064816  0.065047  ...  0.102009  0.102671   
77494       0.065471  0.065499  0.065698  0.066038  ...  0.091097  0.090983   
60614       0.071198  0.071574  0.071992  0.072436  ...  0.088256  0.088113   
79936       0.059363  0.059897  0.060365  0.060832  ...  0.079529  0.079730   

             2017-09   2017-10   2017-11   2017-12   2018-01   2018-02  \
RegionName                                                               
60657       0.089242  0.089402  0.089729  0.090207  0.090712  0.091270   
75070       0.103499  0.104029  0.104327  0.104857  0.105354  0.105851   
77494       0.090870  0.090927  0.091040  0.091154  0.091154  0.091664   
60614       0.088092  0.088373  0.088722  0.088886  0.089139  0.089392   
79936       0.080130  0.080331  0.080331  0.080331  0.080331  0.080464   

             2018-03   2018-04  
RegionName                      
60657       0.091545  0.091261  
75070       0.106348  0.106580  
77494       0.092771  0.093623  
60614       0.089536  0.089433  
79936       0.080798  0.081132  

[5 rows x 172 columns]

In [9]:
# Adding the state information back 
df_scaled["State"] = state_list
df_scaled.head()

2004-01   2004-02   2004-03   2004-04   2004-05   2004-06  \
RegionName                                                               
60657       0.066883  0.067228  0.067653  0.068149  0.068681  0.069238   
75070       0.062166  0.062530  0.063027  0.063524  0.063921  0.064219   
77494       0.065783  0.066152  0.066265  0.066123  0.065868  0.065641   
60614       0.069419  0.069590  0.069829  0.070130  0.070466  0.070828   
79936       0.056091  0.056559  0.057093  0.057694  0.058228  0.058762   

             2004-07   2004-08   2004-09   2004-10  ...   2017-08   2017-09  \
RegionName                                          ...                       
60657       0.069770  0.070239  0.070682  0.071116  ...  0.089216  0.089242   
75070       0.064418  0.064617  0.064816  0.065047  ...  0.102671  0.103499   
77494       0.065471  0.065499  0.065698  0.066038  ...  0.090983  0.090870   
60614       0.071198  0.071574  0.071992  0.072436  ...  0.088113  0.088092   
79936       0.059363  0.059897  0.060365  0.060832  ...  0.079730  0.080130   

             2017-10   2017-11   2017-12   2018-01   2018-02   2018-03  \
RegionName                                                               
60657       0.089402  0.089729  0.090207  0.090712  0.091270  0.091545   
75070       0.104029  0.104327  0.104857  0.105354  0.105851  0.106348   
77494       0.090927  0.091040  0.091154  0.091154  0.091664  0.092771   
60614       0.088373  0.088722  0.088886  0.089139  0.089392  0.089536   
79936       0.080331  0.080331  0.080331  0.080331  0.080464  0.080798   

             2018-04  State  
RegionName                   
60657       0.091261     IL  
75070       0.106580     TX  
77494       0.093623     TX  
60614       0.089433     IL  
79936       0.081132     TX  

[5 rows x 173 columns]

## Visualization Time!

In [11]:
# Using my defined function, found in state_heatmapwithtime.py, to get state-
# level data in the correct format to create a Folium HeatMapWithTime
fl_data = prep_state_data(df_scaled, "FL")

In [12]:
# Again, pre-defined function, this time to get the index for the maps
fl_index = create_index_heatmapwithtime(df_scaled, "FL")

In [13]:
# Creating the folium map, centered at FL
fl_map = folium.Map(location=[27.6648, -81.5158],
                   zoom_start=6, prefer_canvas=True)

plugins.HeatMapWithTime(fl_data, index=fl_index).add_to(fl_map)

fl_map

If you get an output that's just a blank square, the input data is too big for folium. Alas!

In [14]:
# Trying again with a different state
ga_data = prep_state_data(df_scaled, "GA")

In [15]:
# Grabbing the GA index
ga_index = create_index_heatmapwithtime(df_scaled, "GA")

In [16]:
# Creating a new folium map, this time for Georgia
ga_map = folium.Map(location=[32.3656, -82.9001],
                       zoom_start=7, prefer_canvas=True)

plugins.HeatMapWithTime(ga_data, index=ga_index).add_to(ga_map)

ga_map